In [1]:
import pystac_client
from odc import stac as odc_stac
import xarray as xr
import rioxarray
import numpy as np
import hvplot.xarray

from dask_flood_mapper.utils import post_process_eodc_cube, extract_orbit_names

## Dask Client

Dask makes parallel computing easy by providing a familiar API common libraries, such as Pandas and Numpy. This allow efficient scaling of the here presented workflow for this adaptation of the TU Wien Bayesian flood mapping algorithm. The data size will be a main limiting factor as the data grows larger than RAM. For this reason we will partition our data in chunks which will presented to the machine workers by Dasks task scheduler in a most efficient manner. Although many of Dask' settings can be handled automatically, I will set some parameters for optimal performance on my own machine.

I first set the temporary directory for when Dask spills data from the workers memory to disk.

In [2]:
import dask
dask.config.set(temporary_directory='/tmp')

I will then set the Dask Client, where I avoid inter-worker communication which is common for working with `numpy` and `xarray` in this case. Furthermore I selected to work with threading for the reduced time of communication between threads.

In [3]:
from dask.distributed import Client, progress, wait
client = Client(processes=False, threads_per_worker=2,
                n_workers=3, memory_limit='28GB')
client

<Client: 'inproc://128.131.72.130/193992/1' processes=3 threads=6, memory=78.23 GiB>

/home/mschobbe/Documents/projects/dask-flood-mapper/.venv/lib/python3.10/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(
/home/mschobbe/Documents/projects/dask-flood-mapper/.venv/lib/python3.10/site-packages/rasterio/warp.py:344: NotGeoreferencedWarning: Dataset has no geotransform, gcps, or rpcs. The identity matrix will be returned.
  _reproject(


In conjunction with setting up the Dask client I will chunk my arrays along three dimensions according to the following specifications for maximum performance. 

In [4]:
chunks = {'time':1, "latitude": 1300, "longitude": 1300}

## Cube Definitions

The following generic specifications are used for presenting the data.


In [5]:
crs = "EPSG:4326" # Coordinate Reference System - World Geodetic System 1984 (WGS84) in this case 
res = 0.00018 # 20 meter in degree

In [6]:
eodc_catalog = pystac_client.Client.open("https://stac.eodc.eu/api/v1")
eodc_catalog

<Client id=stac-fastapi>

## Northern Germany Flood

Storm Babet hit the Denmark and Northern coast at the 20th of October 2023 [Wikipedia](https://en.wikipedia.org/wiki/Storm_Babet). Here an area around Zingst at the Baltic coast of Northern Germany is selected as the study area.


In [7]:
time_range = "2022-10-11/2022-10-25"
minlon, maxlon = 12.3, 13.1
minlat, maxlat = 54.3, 54.6
bounding_box = [minlon, minlat, maxlon, maxlat]

## EODC STAC Catalog

The `pystac_client` establishes a connection to the EODC STAC Catalog. This results in a catalog object that can be used to discover collections hosted at EODC.

## Microwave Backscatter Measurements

In [8]:
search = eodc_catalog.search(
    collections="SENTINEL1_SIG0_20M",
    bbox=bounding_box,
    datetime=time_range,
)

items_sig0 = search.item_collection()
items_sig0

The state of the orbit and relative orbit number is also saved as the water and land likelihoods calculated later on highly depend on the orbital configuration. These variable will be added as additional coordinates to the data cube. We will also save the scaling factor and nodata value of this item to correct the data accordingly.

In [9]:
bands = "VV"
sig0_dc = odc_stac.load(items_sig0,
                        bands=bands,
                        crs=crs,
                        chunks=chunks,
                        resolution=res,
                        bbox=bounding_box,
                        groupby=None,
                        )
# process add orbit names to cube
sig0_dc = post_process_eodc_cube(sig0_dc, items_sig0, bands).\
    rename_vars({ "VV": "sig0"}).\
    assign_coords(orbit=("time", extract_orbit_names(items_sig0))).\
    dropna(dim="time", how="all").\
    sortby("time")
# remove duplicates from orbits
__, indices = np.unique(sig0_dc.time, return_index=True)
indices.sort()
orbit_sig0 = sig0_dc.orbit[indices].data
# remove duplicates from time dimension by taking the mean
sig0_dc = sig0_dc.groupby("time").mean(skipna=True)
sig0_dc = sig0_dc.assign_coords(orbit=("time", orbit_sig0))
sig0_dc = sig0_dc.persist()
wait(sig0_dc)
sig0_dc

<xarray.Dataset> Size: 237MB
Dimensions:      (time: 8, latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
  * time         (time) datetime64[ns] 64B 2022-10-11T05:25:01 ... 2022-10-23...
    orbit        (time) <U4 128B 'D168' 'A44' 'A44' ... 'A146' 'A146' 'D168'
Data variables:
    sig0         (time, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>

## Harmonic parameters

In [10]:
search = eodc_catalog.search(
    collections="SENTINEL1_HPAR",
    bbox=bounding_box
)

items_hpar = search.item_collection()
items_hpar

In [11]:
bands = ("C1", "C2", "C3", "M0", "S1", "S2", "S3", "STD")
hpar_dc = odc_stac.load(items_hpar,
                        bands=bands,
                        crs=crs,
                        chunks=chunks,
                        resolution=res,
                        bbox=bounding_box,
                        groupby=None,
                        )

hpar_dc = post_process_eodc_cube(hpar_dc, items_hpar, bands).\
    rename({"time": "orbit"})
hpar_dc["orbit"] = extract_orbit_names(items_hpar)
hpar_dc = hpar_dc.groupby("orbit").mean(skipna=True)

Expand parameters along orbit array of sigma naught.


In [12]:
hpar_dc = hpar_dc.sel(orbit = orbit_sig0)
hpar_dc = hpar_dc.persist()
wait(hpar_dc)
hpar_dc

<xarray.Dataset> Size: 2GB
Dimensions:      (orbit: 8, latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
  * orbit        (orbit) object 64B 'D168' 'A44' 'A44' ... 'A146' 'A146' 'D168'
Data variables:
    C1           (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    C2           (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    C3           (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    M0           (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S1           (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S2           (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S3           (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    STD          (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>

## Local Incidence Angles

In [13]:
search = eodc_catalog.search(
    collections="SENTINEL1_MPLIA",
    bbox=bounding_box
)

items_plia = search.item_collection()
items_plia

In [15]:
bands = "MPLIA"
plia_dc = odc_stac.load(items_plia,
                        bands=bands,
                        crs=crs,
                        chunks=chunks,
                        resolution=res,
                        bbox=bounding_box,
                        groupby=None,
                        )

plia_dc = post_process_eodc_cube(plia_dc, items_plia, bands).\
    rename({"time": "orbit"})
plia_dc["orbit"] = extract_orbit_names(items_plia)
plia_dc = plia_dc.groupby("orbit").mean(skipna=True)

Expand parameters along orbit array of sigma naught.

In [16]:
plia_dc = plia_dc.sel(orbit = orbit_sig0)
plia_dc = plia_dc.persist()
wait(plia_dc)
plia_dc

<xarray.Dataset> Size: 237MB
Dimensions:      (orbit: 8, latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
  * orbit        (orbit) object 64B 'D168' 'A44' 'A44' ... 'A146' 'A146' 'D168'
Data variables:
    MPLIA        (orbit, latitude, longitude) float32 237MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>

## Copernicus DEM from Alaska Satellite Facility

In [17]:
cop_alaska_catalog = pystac_client.Client.open("https://stac.asf.alaska.edu/")
cop_alaska_catalog

<Client id=stac-fastapi>

In [18]:
search = cop_alaska_catalog.search(
    collections= "glo-30-hand",
    bbox=bounding_box
)

items_dem = search.item_collection()
print(f"On Alaska we found {len(items_dem)} items for the given search query")
items_dem

On Alaska we found 2 items for the given search query


In [19]:
hand_dc = odc_stac.load(items_dem,
                        crs=crs,
                        chunks=chunks,
                        resolution=res,
                        bbox=bounding_box,
                        resampling="bilinear",
                       ).\
    squeeze("time").\
    drop_vars("time").\
    rename_vars({"data": "hand"})
hand_dc = hand_dc.persist()
wait(hand_dc)
hand_dc

<xarray.Dataset> Size: 30MB
Dimensions:      (latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
Data variables:
    hand         (latitude, longitude) float32 30MB dask.array<chunksize=(1300, 1300), meta=np.ndarray>

## Fuse cube

Here I fuse the four datasets together and filter for the values that have a hand avlue of above zero.

In [35]:
flood_dc = xr.merge([sig0_dc, plia_dc, hpar_dc, hand_dc])
flood_dc = flood_dc.where(flood_dc.hand > 0.001)
flood_dc = flood_dc.\
    reset_index("orbit", drop=True).\
    rename({"orbit": "time"}).\
    dropna(dim="time", how="all", subset=["sig0"])
flood_dc = flood_dc.persist()
wait(flood_dc)
flood_dc

<xarray.Dataset> Size: 2GB
Dimensions:      (time: 6, latitude: 1668, longitude: 4445)
Coordinates:
  * latitude     (latitude) float64 13kB 54.6 54.6 54.6 54.6 ... 54.3 54.3 54.3
  * longitude    (longitude) float64 36kB 12.3 12.3 12.3 12.3 ... 13.1 13.1 13.1
    spatial_ref  int32 4B 4326
  * time         (time) datetime64[ns] 48B 2022-10-11T05:25:01 ... 2022-10-23...
Data variables:
    sig0         (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    MPLIA        (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    C1           (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    C2           (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    C3           (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    M0           (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S1           (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S2           (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    S3           (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    STD          (time, latitude, longitude) float32 178MB dask.array<chunksize=(1, 1300, 1300), meta=np.ndarray>
    hand         (latitude, longitude) float32 30MB dask.array<chunksize=(1300, 1300), meta=np.ndarray>

## Likelihoods

### Water

In [36]:
def calc_water_likelihood(dc):
    return  dc.MPLIA * -0.394181 + -4.142015

In [37]:
flood_dc["wbsc"] = calc_water_likelihood(flood_dc)

### Land

In [38]:
def harmonic_expected_backscatter(dc):
    w = np.pi * 2 / 365
    
    t = dc.time.dt.dayofyear
    wt = w * t
    
    M0 = dc.M0
    S1 = dc.S1
    S2 = dc.S2
    S3 = dc.S3
    C1 = dc.C1
    C2 = dc.C2
    C3 = dc.C3
    hm_c1 = (M0 + S1 * np.sin(wt)) + (C1 * np.cos(wt))
    hm_c2 = ((hm_c1 + S2 * np.sin(2 * wt)) + C2 * np.cos(2 * wt))
    hm_c3 = ((hm_c2 + S3 * np.sin(3 * wt)) + C3 * np.cos(3 * wt))
    return hm_c3

In [39]:
flood_dc["hbsc"] = harmonic_expected_backscatter(flood_dc)

## Flood mapping

In [40]:
def bayesian_flood_decision(dc):
    
    nf_std = 2.754041
    sig0 = dc.sig0
    std = dc.STD
    wbsc = dc.wbsc
    hbsc = dc.hbsc

    f_prob = (1.0 / (std * np.sqrt(2 * np.pi))) * np.exp(-0.5 * \
        (((sig0 - wbsc) / nf_std) ** 2))
    nf_prob = (1.0 / (nf_std * np.sqrt(2 * np.pi))) * np.exp(-0.5 * \
        (((sig0 - hbsc) / nf_std) ** 2))
    
    evidence = (nf_prob * 0.5) + (f_prob * 0.5)
    nf_post_prob = (nf_prob * 0.5) / evidence
    f_post_prob = (f_prob * 0.5) / evidence
    decision = xr.where(np.isnan(f_post_prob) | np.isnan(nf_post_prob), np.nan, np.greater(f_post_prob, nf_post_prob))
    return nf_post_prob, f_post_prob, decision

In [41]:
flood_dc[["nf_post_prob", "f_post_prob", "decision"]] = bayesian_flood_decision(flood_dc)

## Postprocessing

In [42]:
def post_processing(dc):
    dc = dc * np.logical_and(dc.MPLIA >= 27, dc.MPLIA <= 48)
    dc = dc * (dc.hbsc > (dc.wbsc + 0.5 * 2.754041))
    land_bsc_lower = dc.hbsc - 3 * dc.STD
    land_bsc_upper = dc.hbsc + 3 * dc.STD
    water_bsc_upper = dc.wbsc + 3 * 2.754041
    mask_land_outliers = np.logical_and(dc.sig0 > land_bsc_lower, dc.sig0 < land_bsc_upper)
    mask_water_outliers = dc.sig0 < water_bsc_upper
    dc = dc * (mask_land_outliers | mask_water_outliers)
    return  (dc * (dc.f_post_prob > 0.8)).decision

In [43]:
flood_output = post_processing(flood_dc)

## Removal of Speckles

In [ ]:
flood_output = flood_output.rolling({"longitude": 5, "latitude": 5}, center=True).median(skipna=True).persist()
wait(flood_output)
flood_output

## Results

In [ ]:
flood_output.hvplot.quadmesh(x='longitude', y='latitude', geo=True, widget_location='bottom', rasterize=True, \
                            project=True, clim=(0,1), cmap=["rgba(0, 0, 1, 0.1)","darkred"], tiles=True, \
                            clabel="        non-flood                                        flood")